## Predicting the target locations to open a Chinese Restaurant in Pune, India

### Introduction: Business Problem

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening a Chinese restaurant in Pune, India.
Since there are lots of restaurants in Pune we will try to detect locations that are not already crowded with restaurants. We are also particularly interested in areas with no Chinese restaurants in vicinity. We would also prefer locations as close to city centre as possible, assuming that first two conditions are met.
We will use our data science powers to generate a few most promising neighbourhoods based on this criterion. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

### Data

Based on definition of our problem, factors that will influence our decision are:
* number of existing restaurants in the neighbourhood (any type of restaurant)
* number of and distance to Italian restaurants in the neighbourhood, if any
* distance of neighbourhood from city centre





We decided to use regularly spaced grid of locations, centred around city centre, to define our neighbourhoods.
Following data sources will be needed to extract/generate the required information:
* centres of candidate areas will be generated algorithmically and approximate addresses of centres of those areas will be obtained using Geopy Nominatim
* number of restaurants and their type and location in every neighbourhood will be obtained using Foursquare API
* coordinate of Pune centre will be obtained using Geopy Nominatim of well-known Pune location (Shivajinagar)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 20x20 killometers centered around Pune city center.

Let's first find the latitude & longitude of Pune city center, using specific, well known address and Geopy Nominatim.

In [1]:
import warnings
warnings.filterwarnings('ignore')

In [2]:
#!pip install geopy
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

In [3]:
def get_coordinates(address, verbose=False):
    geolocator = Nominatim(user_agent="foursquare_agent")
    location = geolocator.geocode(address)
    latitude = location.latitude
    longitude = location.longitude
    return [latitude, longitude]

address = 'Shivajinagar, Pune, IN'
pune_center = get_coordinates(address)
print('Coordinate of {}: {}'.format(address, pune_center))

Coordinate of Shivajinagar, Pune, IN: [18.5322493, 73.8499601124847]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~10km from Shivajinagar. Our neighborhoods will be defined as circular areas with a radius of 500 meters, so our neighborhood centers will be 1000 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in meters).

In [4]:
#!pip install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Pune center longitude={}, latitude={}'.format(pune_center[1], pune_center[0]))
x, y = lonlat_to_xy(pune_center[1], pune_center[0])
print('Pune center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Pune center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Pune center longitude=73.8499601124847, latitude=18.5322493
Pune center UTM X=7720707.70280034, Y=3664141.8725536014
Pune center longitude=73.84996011248452, latitude=18.5322492999953


Let's create a hexagonal grid of cells: we offset every other row, and adjust vertical row spacing so that every cell center is **equally distant from all it's neighbors.**

In [5]:
pune_center_x, pune_center_y = lonlat_to_xy(pune_center[1], pune_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = pune_center_x - 10000
x_step = 1000
y_min = pune_center_y - 10000 - (int(21/k)*k*1000 - 20000)/2
y_step = 1000 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 500 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(pune_center_x, pune_center_y, x, y)
        if (distance_from_center <= 10001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [6]:
#!pip install folium

import folium

In [7]:
map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.Marker(pune_center, popup='Shivajinagar').add_to(map_pune)
for lat, lon in zip(latitudes, longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='red', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune) 
    folium.Circle([lat, lon], radius=500, color='blue', fill=False).add_to(map_pune)
    #folium.Marker([lat, lon]).add_to(map_pune)
map_pune

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~10km from Shivajinagar.

Let's now use Geopy Nominatim to get approximate addresses of those locations.

In [8]:
print(pune_center[0], pune_center[1])

18.5322493 73.8499601124847


In [9]:
def get_address(latitude, longitude, verbose=False):
    geolocator = Nominatim(user_agent="foursquare_agent")
    address = geolocator.reverse(str(latitude) + "," + str(longitude))
    return address

addr = get_address(pune_center[0], pune_center[1])
print('Reverse geopy check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(pune_center[0], pune_center[1], addr))

Reverse geopy check
-----------------------
Address of [18.5322493, 73.8499601124847] is: Shivajinagar, MSRTC Depot, Shivajinagar, Pune City, Pune District, Maharashtra, 411001, India


In [10]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = str(address).replace(', India', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [11]:
addresses[15:50]

['Sahakar Nagar, Pune City, Pune District, Maharashtra, 411009',
 'Golwalkar Guruji Path, Sahakar Nagar, Pune City, Pune District, Maharashtra, 411009',
 'Kothrud, Pune City, Pune District, Maharashtra, 411038',
 'Kothrud, Pune City, Pune District, Maharashtra, 411038',
 'Kothrud, Pune City, Pune District, Maharashtra, 411038',
 'Kothrud, Pune City, Pune District, Maharashtra, 411038',
 'Karve Nagar, Pune City, Pune District, Maharashtra, PASCHIMANAGARI',
 'Natraj Society, Karve Nagar, Pune City, Pune District, Maharashtra, PASCHIMANAGARI',
 'Navasahyadri Society, Karve Nagar, Pune City, Pune District, Maharashtra, 411001',
 'Dattawadi, Pune City, Pune District, Maharashtra, 411001',
 'Dattawadi, Pune City, Pune District, Maharashtra, 411009',
 'Sahakar Nagar, Pune City, Pune District, Maharashtra, 411009',
 'L. R. Shinde Highschool, Golwalkar Guruji Path, Sahakar Nagar, Pune City, Pune District, Maharashtra, 411009',
 'Shiv Darshan Road, Sahakar Nagar, Pune City, Pune District, Mahara

Looking good. Let's now place all this into a Pandas dataframe.

In [12]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0  Dahanukar Colony (Ram Mandir), , Mavale vasti,...  18.495356  73.810668   
1  CoHive Co-working Space, 188, Karve Road, Mava...  18.492889  73.815545   
2  Mavale vasti, Karve Nagar, Pune City, Pune Dis...  18.490422  73.820421   
3  Prosperity Society, Karve Nagar, Pune City, Pu...  18.487955  73.825297   
4  Prosperity Society, Dattawadi, Pune City, Pune...  18.485488  73.830171   
5  Tukai Nagar, Pune City, Pune District, Maharas...  18.483022  73.835045   
6  Taljai Forest Walking Path, Sahakar Nagar, Pun...  18.480556  73.839918   
7  Kothrud, Pune City, Pune District, Maharashtra...  18.503088  73.805592   
8  Kothrud, Pune City, Pune District, Maharashtra...  18.500620  73.810470   
9  Kothrud, Pune City, Pune District, Maharashtra...  18.498152  73.815347   

              X             Y  Distance from center  
0  7.717708e+06  3.654616e+06           9987.492178  
1  7.718708e+06  3.654616e+06           9733.961167  
2  7.719708e+06  3.654616e+06           9578.622030  
3  7.720708e+06  3.654616e+06           9526.279442  
4  7.721708e+06  3.654616e+06           9578.622030  
5  7.722708e+06  3.654616e+06           9733.961167  
6  7.723708e+06  3.654616e+06           9987.492178  
7  7.716208e+06  3.655482e+06           9759.610648  
8  7.717208e+06  3.655482e+06           9340.770846  
9  7.718208e+06  3.655482e+06           9013.878189

saving this data into local file.

In [13]:
df_locations.to_pickle('./locations.pkl')   

## Foursquare

Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Chinese restaurant' category, as we need info on Chinese restaurants in the neighborhood.


In [18]:
# The code was removed by Watson Studio for sharing.

In [15]:
import requests
# Category IDs corresponding to Chinese restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

chinese_restaurant_categories = ['4bf58dd8d48988d145941735','52af3a5e3cf9994f4e043bea','52af3a723cf9994f4e043bec','52af3a7c3cf9994f4e043bed',
                                 '58daa1558bbb0b01f18ec1d3','52af3a673cf9994f4e043beb','52af3a903cf9994f4e043bee','4bf58dd8d48988d1f5931735',
                                 '52af3a9f3cf9994f4e043bef','52af3aaa3cf9994f4e043bf0','52af3ab53cf9994f4e043bf1','52af3abe3cf9994f4e043bf2',
                                 '52af3ac83cf9994f4e043bf3','52af3ad23cf9994f4e043bf4','52af3add3cf9994f4e043bf5','52af3af23cf9994f4e043bf7',
                                 '52af3ae63cf9994f4e043bf6','52af3afc3cf9994f4e043bf8','52af3b053cf9994f4e043bf9','52af3b213cf9994f4e043bfa',
                                 '52af3b293cf9994f4e043bfb','52af3b343cf9994f4e043bfc','52af3b3b3cf9994f4e043bfd','52af3b463cf9994f4e043bfe',
                                 '52af3b633cf9994f4e043c01','52af3b513cf9994f4e043bff','52af3b593cf9994f4e043c00','52af3b6e3cf9994f4e043c02',
                                 '52af3b773cf9994f4e043c03','52af3b813cf9994f4e043c04','52af3b893cf9994f4e043c05','52af3b913cf9994f4e043c06',
                                 '52af3b9a3cf9994f4e043c07','52af3ba23cf9994f4e043c08']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse', 'hotel']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', India', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=1000, limit=100):
    version = '20210324'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [22]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found chinese restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=550 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=550, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_chinese = is_restaurant(venue_categories, specific_filter=chinese_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_chinese, x, y)
                if venue_distance<=500:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_chinese:
                    chinese_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, chinese_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
chinese_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('chinese_restaurants.pkl', 'rb') as f:
        chinese_restaurants = pickle.load(f)
    with open('location_restaurants.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, chinese_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('chinese_restaurants.pkl', 'wb') as f:
        pickle.dump(chinese_restaurants, f)
    with open('location_restaurants.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
        

Restaurant data loaded.
Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [23]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Chinese restaurants:', len(chinese_restaurants))
print('Percentage of Chinese restaurants: {:.2f}%'.format(len(chinese_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 576
Total number of Chinese restaurants: 42
Percentage of Chinese restaurants: 7.29%
Average number of restaurants in neighborhood: 3.3873626373626373


In [24]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4bb4d5eb6444b713c5b6f300', "Sudit Su's Chinese", 18.495267323913957, 73.812487704967, 'Dahanukar Colony, Lane No 3 (Kothrud), Pune 411029, Mahārāshtra', 440, True, 7718006.777898461, 3654755.0717524327)
('4c599efcec2520a1d3794f12', 'Mirch Masala', 18.493548696997465, 73.81403641572999, 'Near Dahanukar Colony (Off Karve road), Pune, Mahārāshtra', 530, False, 7718407.521370351, 3654598.2088460224)
('4e58a1b4c65bcd7cbe2923b6', 'Hotel Pruthvi', 18.494653067145514, 73.81342936618688, 'Happy Colony (Near Dhanukar), Pune 411029, Mahārāshtra', 438, False, 7718212.126185601, 3654731.9486471564)
('4dc4183452b1e8f9f7b17a21', 'the kolhapur darbar', 18.49869609678444, 73.81392009736659, 'opp.kothrud bus-stand (karve road), Pune 411013, Mahārāshtra', 541, False, 7717931.003475635, 3655451.7822320717)
('54116b47498e6ec0ab527125', 'Masti Misal', 18.49838143462304, 73.81425900011426, 'Kothrud', 117, False, 7718013.232752127, 3655427.7681971663)
('4da1be

In [25]:
print('List of Chinese restaurants')
print('---------------------------')
for r in list(chinese_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(chinese_restaurants))

List of Chinese restaurants
---------------------------
('4bb4d5eb6444b713c5b6f300', "Sudit Su's Chinese", 18.495267323913957, 73.812487704967, 'Dahanukar Colony, Lane No 3 (Kothrud), Pune 411029, Mahārāshtra', 440, True, 7718006.777898461, 3654755.0717524327)
('4d8f77d6d00a6ea819e1cf4f', 'Bavdhan Chawpati', 18.50355976681708, 73.8110997147573, 'chandni chowk, Pune 411038, Mahārāshtra', 427, True, 7717047.000812298, 3656028.140188185)
('4ec68d8429c22cc60b39acad', 'Himalaya Chinese', 18.50790728978584, 73.79737060016012, '411038, Mahārāshtra', 464, True, 7714463.941060647, 3655592.253142708)
('4fdf6313e4b044d93c5fbaae', 'Hotel Moonlight Chinese', 18.504075602418958, 73.82108816289505, 'Maruti Mandir, Karishma Soc. Chawk (Karve Road), Pune 411029, Mahārāshtra', 383, True, 7718599.369650144, 3656962.658331739)
('4e0363ff227144bc81ceb8ef', 'New China Town', 18.49942251835569, 73.8309942097594, 'India', 371, True, 7720598.986736644, 3657023.5223525935)
('4f47a9e5e4b0e13228e4bda9', 'A-1 Chin

In [26]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: 
Restaurants around location 102: 
Restaurants around location 103: Baba Food Mall
Restaurants around location 104: Casalolo
Restaurants around location 105: Panchvati Gaurav, Hotel Roopali, Wadeshwar, Vaishali | वैशाली, Darshan foods, Janaseva Bhojanalaya, Top In Town, Horn OK Please
Restaurants around location 106: Sukanta, Aware Maratha Khanawal, Darshan foods, Wadeshwar, Janaseva Bhojanalaya, Top In Town, Mathura restaurant, Hotel Shreyas
Restaurants around location 107: Bhagat Tarachand, Aware Maratha Khanawal, Poona Boarding House, Badshahi Mess, Bedekar Misal, Durvankur Dining Hall, Badshahi Boarding House, Sanskruti Restaurant
Restaurants around location 108: Shree Wadeshwar Bhuvan, SP Biryani House, Ganraj Restaurant, Masemari, Badshahi Mess, Poona Boarding House, Badshahi Boarding House, Rassa - Jasa Hawa Tassa
Restaurants around location 109: Jayshree Garden, Jayashree Paavbhaji, Ganraj 

Let's now see all the collected restaurants in our area of interest on map, and let's also show Chinese restaurants in different color.

In [29]:
map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.Marker(pune_center, popup='Shivajinagar').add_to(map_pune)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_chinese = res[6]
    color = 'red' if is_chinese else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_pune)
map_pune

Looking good. So now we have all the restaurants in area within few kilometers from Shivajinagar, and we know which ones are Chinese restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Chinese restaurant!

## Methodology

In this project we will direct our efforts on detecting areas of Pune that have low restaurant density, particularly those with low number of Chinese restaurants. We will limit our analysis to area ~10km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 10km from Pune center (Shivajinagar).** We have also **identified Chinese restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of **'restaurant density'** across different areas of Pune - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (and no Chinese restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 500 meters**, and we want **locations without Italian restaurants in radius of 800 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's **count the number of restaurants in every area candidate:**

In [30]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=500m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=500m: 3.3873626373626373


Address   Latitude  Longitude  \
0  Dahanukar Colony (Ram Mandir), , Mavale vasti,...  18.495356  73.810668   
1  CoHive Co-working Space, 188, Karve Road, Mava...  18.492889  73.815545   
2  Mavale vasti, Karve Nagar, Pune City, Pune Dis...  18.490422  73.820421   
3  Prosperity Society, Karve Nagar, Pune City, Pu...  18.487955  73.825297   
4  Prosperity Society, Dattawadi, Pune City, Pune...  18.485488  73.830171   
5  Tukai Nagar, Pune City, Pune District, Maharas...  18.483022  73.835045   
6  Taljai Forest Walking Path, Sahakar Nagar, Pun...  18.480556  73.839918   
7  Kothrud, Pune City, Pune District, Maharashtra...  18.503088  73.805592   
8  Kothrud, Pune City, Pune District, Maharashtra...  18.500620  73.810470   
9  Kothrud, Pune City, Pune District, Maharashtra...  18.498152  73.815347   

              X             Y  Distance from center  Restaurants in area  
0  7.717708e+06  3.654616e+06           9987.492178                    3  
1  7.718708e+06  3.654616e+06           9733.961167                    4  
2  7.719708e+06  3.654616e+06           9578.622030                    0  
3  7.720708e+06  3.654616e+06           9526.279442                    4  
4  7.721708e+06  3.654616e+06           9578.622030                    4  
5  7.722708e+06  3.654616e+06           9733.961167                    0  
6  7.723708e+06  3.654616e+06           9987.492178                    0  
7  7.716208e+06  3.655482e+06           9759.610648                    7  
8  7.717208e+06  3.655482e+06           9340.770846                    7  
9  7.718208e+06  3.655482e+06           9013.878189                   11

OK, now let's calculate the **distance to nearest Chinese restaurant from every area candidate center** (not only those within 500m - we want distance to closest one, regardless of how distant it is).

In [31]:
distances_to_chinese_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in chinese_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_chinese_restaurant.append(min_distance)

df_locations['Distance to Chinese restaurant'] = distances_to_chinese_restaurant

In [32]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  Dahanukar Colony (Ram Mandir), , Mavale vasti,...  18.495356  73.810668   
1  CoHive Co-working Space, 188, Karve Road, Mava...  18.492889  73.815545   
2  Mavale vasti, Karve Nagar, Pune City, Pune Dis...  18.490422  73.820421   
3  Prosperity Society, Karve Nagar, Pune City, Pu...  18.487955  73.825297   
4  Prosperity Society, Dattawadi, Pune City, Pune...  18.485488  73.830171   
5  Tukai Nagar, Pune City, Pune District, Maharas...  18.483022  73.835045   
6  Taljai Forest Walking Path, Sahakar Nagar, Pun...  18.480556  73.839918   
7  Kothrud, Pune City, Pune District, Maharashtra...  18.503088  73.805592   
8  Kothrud, Pune City, Pune District, Maharashtra...  18.500620  73.810470   
9  Kothrud, Pune City, Pune District, Maharashtra...  18.498152  73.815347   

              X             Y  Distance from center  Restaurants in area  \
0  7.717708e+06  3.654616e+06           9987.492178                    3   
1  7.718708e+06  3.654616e+06           9733.961167                    4   
2  7.719708e+06  3.654616e+06           9578.622030                    0   
3  7.720708e+06  3.654616e+06           9526.279442                    4   
4  7.721708e+06  3.654616e+06           9578.622030                    4   
5  7.722708e+06  3.654616e+06           9733.961167                    0   
6  7.723708e+06  3.654616e+06           9987.492178                    0   
7  7.716208e+06  3.655482e+06           9759.610648                    7   
8  7.717208e+06  3.655482e+06           9340.770846                    7   
9  7.718208e+06  3.655482e+06           9013.878189                   11   

   Distance to Chinese restaurant  
0                      330.000311  
1                      714.667761  
2                     1706.634059  
3                     2410.382213  
4                     2650.919565  
5                     3200.750953  
6                     3808.812279  
7                     1001.552341  
8                      569.658729  
9                      753.817627

In [34]:
print('Average distance to closest Chinese restaurant from each area center:', df_locations['Distance to Chinese restaurant'].mean())

Average distance to closest Chinese restaurant from each area center: 1748.6205722720654


OK, so on **average Chiense restaurant can be found within ~2KM** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's create a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show **borders of Pune boroughs** on our map and a few circles indicating distance of 3km, 4km and 5km from Shivajinagar.

In [36]:
pune_boroughs_url = 'https://raw.githubusercontent.com/datameet/Municipal_Spatial_Data/master/Pune/pune-electoral-wards_current.geojson'
pune_boroughs = requests.get(pune_boroughs_url).json()

def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

In [37]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

chinese_latlons = [[res[2], res[3]] for res in chinese_restaurants.values()]

In [38]:
from folium import plugins
from folium.plugins import HeatMap

map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_pune) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
folium.Circle(pune_center, radius=3000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=4000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=5000, fill=False, color='white').add_to(map_pune)
folium.GeoJson(pune_boroughs, style_function=boroughs_style, name='geojson').add_to(map_pune)
map_pune

Looks like a few pockets of low restaurant density closest to city center can be found **north and south from Shivajinagar**. 

Let's create another heatmap map showing **heatmap/density of Chinese restaurants** only.

In [39]:
from folium import plugins
from folium.plugins import HeatMap

map_pune = folium.Map(location=pune_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_pune) #cartodbpositron cartodbdark_matter
HeatMap(chinese_latlons).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
folium.Circle(pune_center, radius=3000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=4000, fill=False, color='white').add_to(map_pune)
folium.Circle(pune_center, radius=5000, fill=False, color='white').add_to(map_pune)
folium.GeoJson(pune_boroughs, style_function=boroughs_style, name='geojson').add_to(map_pune)
map_pune

This map is not so 'hot' (Chinese restaurants represent a subset of ~7% of all restaurants in Pune) but it also indicates higher density of existing Chinese restaurants directly east and west from Shivajinagar, with closest pockets of **low Chinese restaurant density positioned north and south from city center**.

Based on this we will now focus our analysis on areas *north and south from Pune center* - we will move the center of our area of interest and reduce it's size to have a radius of **4 km**. This places our location candidates mostly in boroughs of **Swargate**. Another potentially interesting borough is **Mandalay Lines** with large low restaurant density north from city center, however this borough is less interesting to stakeholders as it's a military area where the interest of people in such venues is very less.

## Swargate

**Swargate** is one of the **busiest** area in Pune. It has a major bus stand and houses many **important buildings** like Income Tax office. It will also server as major head for the Pune Metro project. There are many places **tourist places and entertainment places** in the area of Swargate which makes it one of the popular area in Pune.

Based on these it appears that this place appear to justify our analysis.

Let's define new, more narrow region of interest, which will include low-restaurant-count parts of Swargate closest to Shivajinagar.

In [54]:
roi_x_min = pune_center_x-2000
roi_y_max = pune_center_y+2000
roi_width = 4000
roi_height = 4000
roi_center_x = roi_x_min + 4000
roi_center_y = roi_y_max - 4000
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_pune = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
folium.Circle(roi_center, radius=4000, color='white', fill=True, fill_opacity=0.4).add_to(map_pune)
folium.GeoJson(pune_boroughs, style_function=boroughs_style, name='geojson').add_to(map_pune)
map_pune

Not bad - this nicely covers all the pockets of low restaurant density in Swargate closest to Pune center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 300m appart).

In [55]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 300
y_step = 300 * k 
roi_y_min = roi_center_y - 4000

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 150 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

251 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **500 meters**) and **distance to closest Chinese restaurant**.

In [56]:
def count_restaurants_nearby(x, y, restaurants, radius=500):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_chinese_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=500)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, chinese_restaurants)
    roi_chinese_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [57]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Chinese restaurant':roi_chinese_distances})

df_roi_locations.head(10)

Latitude  Longitude             X             Y  Restaurants nearby  \
0  18.507281  73.846981  7.722458e+06  3.659701e+06                   4   
1  18.506540  73.848443  7.722758e+06  3.659701e+06                   4   
2  18.505799  73.849904  7.723058e+06  3.659701e+06                   3   
3  18.510341  73.843999  7.721708e+06  3.659961e+06                   3   
4  18.509600  73.845461  7.722008e+06  3.659961e+06                   4   
5  18.508859  73.846923  7.722308e+06  3.659961e+06                   7   
6  18.508118  73.848385  7.722608e+06  3.659961e+06                   7   
7  18.507377  73.849846  7.722908e+06  3.659961e+06                   5   
8  18.506636  73.851308  7.723208e+06  3.659961e+06                   4   
9  18.505895  73.852769  7.723508e+06  3.659961e+06                   6   

   Distance to Chinese restaurant  
0                     2291.656940  
1                     2490.681430  
2                     2697.413576  
3                     1669.265606  
4                     1844.448441  
5                     2006.124639  
6                     2197.062147  
7                     2410.317011  
8                     2640.487476  
9                     2883.525641

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 500 meters**, and **no Chinese restaurants in radius of 800 meters**.

In [58]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to Chinese restaurant']>=800)
print('Locations with no Italian restaurants within 800m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 149
Locations with no Italian restaurants within 800m: 226
Locations with both conditions met: 148


Let's see how this looks on a map.

In [59]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_pune = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_pune)
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Circle(roi_center, radius=4000, color='white', fill=True, fill_opacity=0.6).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune) 
folium.GeoJson(pune_boroughs, style_function=boroughs_style, name='geojson').add_to(map_pune)
map_pune

Looking good. We now have a bunch of locations fairly close to Shivajinagar (mostly in Swargate and south-east from Swargate), and we know that each of those locations has no more than two restaurants in radius of 500m, and no Chinese restaurant closer than 800m. Any of those locations is a potential candidate for a new Chinese restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [60]:
map_pune = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)
folium.GeoJson(pune_boroughs, style_function=boroughs_style, name='geojson').add_to(map_pune)
map_pune

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Chinese restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [62]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_pune = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_pune)
HeatMap(restaurant_latlons).add_to(map_pune)
folium.Circle(roi_center, radius=4000, color='white', fill=True, fill_opacity=0.4).add_to(map_pune)
folium.Marker(pune_center).add_to(map_pune)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=800, color='green', fill=True, fill_opacity=0.25).add_to(map_pune) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)
folium.GeoJson(pune_boroughs, style_function=boroughs_style, name='geojson').add_to(map_pune)
map_pune

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [63]:
map_punr = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(pune_center).add_to(map_punr)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=500, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_punr)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_punr)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=800, color='green', fill=False).add_to(map_punr) 
folium.GeoJson(pune_boroughs, style_function=boroughs_style, name='geojson').add_to(map_punr)
map_punr

Let's zoom in on candidate areas in **Swargate**:

In [66]:
map_pune = folium.Map(location=[18.5018, 73.8636], zoom_start=15)
folium.Marker(pune_center).add_to(map_pune)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_pune) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_pune)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_pune)
folium.GeoJson(pune_boroughs, style_function=boroughs_style, name='geojson').add_to(map_pune)
map_pune

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [68]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = str(get_address(lat, lon)).replace(', India', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, pune_center_x, pune_center_y)
    print('{}{} => {:.1f}km from Shivajinagar'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

Mangalwar Peth, Pune City, Pune District, Maharashtra, 411011 => 2.6km from Shivajinagar
Guruwar Peth, Pune City, Pune District, Maharashtra, 411002 => 4.7km from Shivajinagar
Bhau Rangari Path, Shaniwar Peth, Pune City, Pune District, Maharashtra, 411002 => 2.9km from Shivajinagar
COEP Hostel, Dr. Rajendra Prasad Path, Shivajinagar, Pune City, Pune District, Maharashtra, 411002 => 0.7km from Shivajinagar
U.J. Solanki, Maulana Abul Kalam Azad Path, Guruwar Peth, Pune City, Pune District, Maharashtra, 411002 => 3.9km from Shivajinagar
Chhatrapati Sambhaji Path, Deccan Gymkhana, Pune City, Pune District, Maharashtra, 411004 => 3.6km from Shivajinagar
Ganesh Peth, Pune City, Pune District, Maharashtra, 411001 => 4.3km from Shivajinagar
Kasba Peth, Pune City, Pune District, Maharashtra, 411001 => 2.4km from Shivajinagar
Agarkar Madhyamik Vidyalay, Sardar Moodliar Path, Somwar Peth, Pune City, Pune District, Maharashtra, 411002

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Chinese restaurants nearby, all zones being fairly close to city center (all less than 6km from Shivajinagar, and about half of those less than 4km from Shivajinagar). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in Swargate boroughs, which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

In [69]:
map_pune = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(pune_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_pune)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_pune) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_pune)
map_pune

## Results and Discussion

Our analysis shows that although there is a great number of restaurants in Pune (~600 in our initial area of interest which was 20x20km around Shivajinagar), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected east and west from Shivajinagar, so we focused our attention to areas south and north, corresponding to boroughs Swargate and south-east of Shivajinagar. Another borough was identified as potentially interesting (Mandalay Lane, north from Shivajinagar), but our attention was focused on Swargate which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics and a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest (covering approx. 5x5km south from Shivajinagar) we first created a dense grid of location candidates (spaced 300m appart); those locations were then filtered so that those with more than two restaurants in radius of 500m and those with an Chinese restaurant closer than 800m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Chinese restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Pune center but not crowded with existing restaurants (particularly Chinese) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion

Purpose of this project was to identify Pune areas close to center with low number of restaurants (particularly Chinese restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Chinese restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (Swargate), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.